In [ ]:
def Clogit_hess(b,Xbig,ybig,k,J,N,mu0,V0):

    b.shape=(len(b),1) #else trouble for prior chunk, will turn 2 x 2, since b comes in as a (2,)
    
    int1=exp(Xbig @ b) #N*J by 1 - each row = xij'beta
    int2=(int1.reshape(N,J)).T #J by N - note reshape collects over rows first, so we first reshaped "the wrong way", then transposed
    #sum for each triplet
    denom = sum(int2,axis=0) #N by 1
    denom.shape=(1,N) #turn into a row vector
    
    #replicate each element in denom j times
    int3=repeat(denom,J) #looks good
    int3.shape=(N*J,1)

    giantP=int1/int3  #OK, shape is 3000 x 1 (N*j by 1), max<1; same construct as for gradient

    # try slow, but clear way first
    #reshape to N cells @ J by 1's
    intcell=giantP.reshape(N,J,1)
    Xcell=Xbig.reshape(N,J,k)

    intsum=zeros([k,k])
    for i in range(0,N):
        Pi=intcell[i-1] #J by 1
        Xi=Xcell[i-1] # J by k
        li=diagflat(Pi)-Pi @ Pi.T   #need to "flatten" vector to construct diagonal matrix
        intsum = intsum+Xi.T @ li @ Xi
    
    H=-(-inv(V0) - intsum) # k by k
    
    return(H)